### Colorectal Cancer Dataset

In [1]:
# load modules
import pandas as pd
from src import read
from src import preprocessing
from src import eda
from src import experimental

### Data Load

In [2]:
# define data folder path and data file names

raw_data_folder = r"C:\Users\35799\Desktop\cookiecutter-analytical-project\biolizard-internship-marios\data\raw"
gene_expression_data = r"Colorectal Cancer Gene Expression Data.csv"
patient_data = r"Colorectal Cancer Patient Data.csv"

In [3]:
# load data

gene_expression_df = read.data_load(folder=raw_data_folder, filename=gene_expression_data)
patient_df = read.data_load(folder=raw_data_folder, filename=patient_data)

In [4]:
# combine data into one Pandas DataFrame

gene_expression_df_transposed = gene_expression_df.transpose()
gene_expression_df_transposed.columns = gene_expression_df_transposed.iloc[0]
gene_expression_df_transposed_index = gene_expression_df_transposed.drop("ID_REF", axis=0)
gene_expression_df_transposed_index_final = gene_expression_df_transposed_index.astype("float64")
df = pd.merge(patient_df, gene_expression_df_transposed_index_final, right_index=True, left_on='ID_REF')

In [5]:
# data info

df_id, df_cat, df_cont = read.data_info(df, threshold=20)

DIMENSIONS:
----------------------------------------------------------------------------------------------------
Entries: 62
Features: 1944
----------------------------------------------------------------------------------------------------


CATEGORICAL FEATURES:
----------------------------------------------------------------------------------------------------
Features     Data Type    Categories & Counts
-----------  -----------  ---------------------------------------------------
Dukes Stage  object       {'A': 16, 'B': 14, 'C': 20, 'D': 12}
Gender       object       {'Female': 14, 'Male': 48}
Location     object       {'Colon': 2, 'Left': 20, 'Rectum': 18, 'Right': 22}
DFS event    float64      {0.0: 25, 1.0: 37}
Adj_Radio    float64      {0.0: 29, 1.0: 33}
Adj_Chem     float64      {0.0: 32, 1.0: 30}
----------------------------------------------------------------------------------------------------


CONTINUOUS FEATURES:
---------------------------------------------------------

In [6]:
df = df.drop(df[df["Location"] == "Colon"].index)

### Data Preprocessing

In [7]:
# data split

X, y, X_train, y_train, X_test, y_test, X_val, y_val = preprocessing.data_split(df, target="Dukes Stage", method="tt", train_proportion=0.8, validation_proportion=0.25, stratify=True, random_state=0)

In [8]:
# treat missing values

train_df, test_df = preprocessing.treat_nan(X_train, y_train, X_test, y_test, df_id, df_cat, df_cont, target="Dukes Stage", drop_nan_rows=False, impute_cutoff=0.5, categorical_imputer="mode", continuous_imputer="median")

In [9]:
# treat duplicate values

train_df, test_df = preprocessing.treat_duplicate(train_df, test_df, keep_in="first")

In [10]:
# treat outliers

train_df, test_df = preprocessing.treat_outliers(train_df, test_df, df_id, df_cat, df_cont, target="Dukes Stage", method="svm", outlier_fraction=0.35)

The following entries are probable outliers as identified by the One-class Support Vector Machine technique (train set):


ID_REF  Gender Location  DFS event  Adj_Radio  Adj_Chem  \
39  GSM877165    Male     Left        0.0        0.0       1.0   
27  GSM877153    Male   Rectum        1.0        1.0       0.0   
55  GSM877182    Male    Right        1.0        0.0       0.0   
21  GSM877147    Male    Right        0.0        0.0       0.0   
45  GSM877171    Male    Right        1.0        0.0       1.0   
59  GSM877186    Male     Left        1.0        1.0       0.0   
43  GSM877169  Female     Left        0.0        0.0       0.0   
12  GSM877138    Male    Right        0.0        0.0       1.0   
52  GSM877179    Male     Left        0.0        1.0       1.0   
20  GSM877146    Male   Rectum        0.0        1.0       1.0   
8   GSM877134    Male    Right        0.0        1.0       1.0   
35  GSM877161    Male    Right        0.0        1.0       0.0   
28  GSM877154    Male   Rectum        1.0        1.0       0.0   
16  GSM877142    Male    Right        1.0        0.0       1.0   
24  GSM877150    Male   Rectum        1.0        0.0       1.0   
17  GSM877143    Male    Right        0.0        1.0       0.0   
9   GSM877135  Female   Rectum        0.0        0.0       0.0   

    Age (in years)  DFS (in months)     117_at  1007_s_at   1053_at    121_at  \
39            46.0             15.0   5.774617  10.297960  7.067800  7.717166   
27            61.0             14.0  10.368146  10.761687  7.237572  7.683509   
55            55.0             14.0   5.407188  10.585953  7.776103  6.898353   
21            28.0             85.0   8.402295   9.754302  8.191826  8.588304   
45            73.0             24.0   4.472217  10.610713  6.754314  7.512881   
59            65.0             25.0   8.661629  10.427298  7.512632  7.046389   
43            44.0             66.0   4.952005  10.136909  7.655282  7.302708   
12            47.0             81.0   7.006106  10.033355  8.553709  7.730508   
52            60.0             14.0   5.111097  10.084649  6.119306  7.267976   
20            50.0             91.0   6.420283  10.225935  7.505152  7.113644   
8             54.0             80.0   4.903302  10.551750  7.869727  7.462846   
35            63.0             17.0   4.636176  10.064616  7.701012  7.412851   
28            66.0             13.0   5.568210  10.446765  7.385270  7.875053   
16            70.0            103.0   6.004252   7.754544  6.795014  7.014675   
24            74.0             11.0   4.908442  10.376543  8.104784  7.249637   
17            67.0              4.0   6.468004  10.214872  7.450276  7.205786   
9             68.0             94.0   6.530134  10.165121  7.615570  7.476847   

    1255_g_at   1294_at   1316_at   1320_at  1405_i_at   1431_at   1438_at  \
39   3.572938  6.694061  6.132715  3.858564   6.733462  3.327047  5.519454   
27   2.837354  8.969693  6.081014  4.140208  10.461856  3.418025  5.845527   
55   2.881039  7.106121  5.791258  4.019104   7.345634  3.466989  5.876684   
21   3.093167  6.654735  5.754420  4.062427   9.128890  3.451669  4.707356   
45   3.010147  7.829368  6.216812  4.049242   7.263656  3.409415  8.631392   
59   2.650723  5.992824  5.285014  4.047409   5.335867  3.381974  6.081336   
43   2.915706  8.122575  5.967239  3.846037   7.828439  3.377166  7.660930   
12   2.953688  7.183682  6.294097  3.985674   9.058086  3.308840  7.604331   
52   2.741116  8.101274  5.658214  3.979695   9.140687  3.221388  5.462382   
20   2.950536  7.187298  6.178597  3.688796   9.066562  3.305809  6.858216   
8    3.066619  6.982733  5.781327  3.784000   6.687646  3.349103  7.496297   
35   3.186199  7.510427  5.766115  3.829780   5.469602  3.408081  7.006718   
28   2.992019  6.835082  6.140051  3.735254   7.569299  3.560199  7.694217   
16   3.242701  7.833150  5.453137  3.913796  10.774562  3.419892  5.053987   
24   2.927889  6.674732  6.168213  3.896253   5.016757  3.288931  8.154682   
17   2.969755  7.172667  6.345145  3.720011   8.988367  3.476634  6.992055   
9    2.971537  7.682610  6.450320

The following entries are probable outliers as identified by the One-class Support Vector Machine technique (test set):


ID_REF Gender Location  DFS event  Adj_Radio  Adj_Chem  Age (in years)  \
48  GSM877175   Male     Left        1.0        1.0       0.0            56.0   
40  GSM877166   Male     Left        1.0        1.0       1.0            78.0   
49  GSM877176   Male   Rectum        1.0        1.0       0.0            59.0   
11  GSM877137   Male    Right        0.0        1.0       0.0            68.0   
0   GSM877126   Male     Left        0.0        1.0       0.0            62.0   

    DFS (in months)    117_at  1007_s_at   1053_at    121_at  1255_g_at  \
48             12.0  4.792020  10.704085  7.718933  7.096596   2.784996   
40             17.0  4.664240  10.156231  7.726520  7.917791   3.028881   
49             17.0  4.981115  10.050384  7.794651  7.226638   3.370863   
11            106.0  5.051468  10.159113  7.384296  7.443270   2.904777   
0             108.0  6.029834   9.468893  7.187090  6.807582   3.084591   

     1294_at   1316_at   1320_at  1405_i_at   1431_at   1438_at   1487_at  \
48  7.301731  5.739711  4.002761   8.344025  3.420608  6.846713  8.837433   
40  7.568330  5.622042  3.855261   4.685060  3.376070  7.068375  8.258589   
49  7.205589  5.987415  3.819068   7.245033  3.161110  8.419512  7.760497   
11  6.961102  6.142163  3.586663   7.515161  3.586601  7.928265  8.608508   
0   7.397013  6.525426  3.848253   7.572331  3.748200  6.957488  8.057704   

    1494_f_at  1552256_a_at  1552257_a_at  1552258_at  1552261_at  1552263_at  \
48   4.503762      8.202261      9.512934    4.451526    3.366267    6.186895   
40   4.337713      8.422382      8.838345    4.082848    3.270576    5.893482   
49   4.496165      7.587643      8.420991    4.042019    3.417658    6.288110   
11   4.201323      8.808424      8.724399    4.372757    3.287648    5.928472   
0    4.311960      7.246198      8.998012    3.912720    4.206709    6.293766   

    1552264_a_at  1552266_at  1552269_at  1552271_at  1552272_a_at  \
48      6.857042    2.982286    2.956672    4.620759      4.529428   
40      6.322052    4.078892    2.852943    4.452060      3.903899   
49      6.782065    3.575495    2.859010    4.573116      4.682545   
11      6.466866    2.728882    2.999134    4.934951      4.838923   
0       6.585635    2.837637    3.024119    4.561616      4.371035   

    1552274_at  1552275_s_at  1552276_a_at  1552277_a_at  1552278_a_at  \
48    6.144479      5.342325      4.064762      6.868444      4.465585   
40    6.226961      4.582948      4.132260      7.685542      4.350138   
49    5.735883      4.420431      4.444720      7.102145      4.008223   
11    5.856147      4.425130      4.188268      6.187011      4.616938   
0     6.120874      4.361976      4.765517      7.101751      3.900317   

    1552279_a_at  1552280_at  1552281_at  1552283_s_at  1552286_at  \
48      5.234004    2.909716    8.246189      7.405030    4.962862   
40      5.542424    3.045678    7.969821      4.365200    5.714887   
49      5.013315    3.025482    6.601371      5.024039    5.273995   
11      5.714469    3.100541    8.669562      3.357916    5.997631   
0       5.035382    2.830732    6.470622      3.906776    5.081563   

    1552287_s_at  1552288_at  1552289_a_at  1552291_at  1552293_at  \
48      6.804328    3.491802      4.192631    6.924439    3.787885   
40      6.275560    3.184562      4.099147    6.782487    4.026074   
49      6.950271    3.118505      3.905340    6.846237    3.636346   
11      7.228586    2.972889      4.240298    7.267790    3.578814   
0       6.837268    3.297914      4.153212    6.358204    3.360942   

    1552295_a_at  1552296_at  1552299_at  1552301_a_at  1552302_at  \
48      6.220880    3.271156    4.791710      3.731796    3.379070   
40      5.893130    3.579156    4.307090      3.762485    3.347975   
49      6.359424    3.848267    4.205405      4.130198    3.664951   
11      6.009598    3.197234    5.069212      3.848721    2.958439   
0       5.999121    3.611584    4.041372      3.673284    4.4

In [11]:
# target feature imbalance check

preprocessing.target_balance_check(train_df, target="Dukes Stage", imbalance_fraction=0.5, graphic=False)

Target Feature Levels      Counts    Percentages
-----------------------  --------  -------------
A                               8          0.258
B                               7          0.226
C                              11          0.355
D                               5          0.161


The tagret feature levels are balanced.


In [12]:
### sampling to treat target feature imbalance

# oversampling ratios must be greater or equal to 1
oversampling_ratios = {"A": 1.2, "B": 1.2, "C": 1.2, "D": 1.2}
train_df_oversampled = preprocessing.sampler(train_df, target="Dukes Stage", method="over", sampling_ratios=oversampling_ratios, random_state=0, graphic=False)

Balanced target feature (oversampling):
Target Feature Levels      Counts    Percentages
-----------------------  --------  -------------
A                              14           0.25
B                              14           0.25
C                              14           0.25
D                              14           0.25


In [13]:
### sampling to treat target feature imbalance

# undersampling ratios must be less or equal to 1
undersampling_ratios = {"A": 0.8, "B": 0.8, "C": 0.8, "D": 0.8}
train_df_undersampled = preprocessing.sampler(train_df, target="Dukes Stage", method="under", sampling_ratios=undersampling_ratios, random_state=0, graphic=False)

Balanced target feature (undersampling):
Target Feature Levels      Counts    Percentages
-----------------------  --------  -------------
A                               4           0.25
B                               4           0.25
C                               4           0.25
D                               4           0.25


### Data Exploration

In [14]:
# data sample for examples

continuous_df = train_df.loc[:, df_cont]
slice = continuous_df.iloc[:, 2:10]

In [15]:
# correlation matrix

pearson_corr_matrix = eda.correlations(slice, type="pearson", printout="matrix")

Pearson Correlation Matrix:


117_at  1007_s_at  1053_at  121_at  1255_g_at  1294_at  1316_at  \
117_at      1.000     -0.397    0.200  -0.407      0.174   -0.080   -0.309   
1007_s_at  -0.397      1.000    0.076   0.066     -0.005   -0.167    0.069   
1053_at     0.200      0.076    1.000  -0.077     -0.167   -0.267   -0.438   
121_at     -0.407      0.066   -0.077   1.000     -0.489    0.023    0.158   
1255_g_at   0.174     -0.005   -0.167  -0.489      1.000   -0.016   -0.206   
1294_at    -0.080     -0.167   -0.267   0.023     -0.016    1.000   -0.083   
1316_at    -0.309      0.069   -0.438   0.158     -0.206   -0.083    1.000   
1320_at     0.378     -0.271    0.152  -0.300      0.208    0.153   -0.134   

           1320_at  
117_at       0.378  
1007_s_at   -0.271  
1053_at      0.152  
121_at      -0.300  
1255_g_at    0.208  
1294_at      0.153  
1316_at     -0.134  
1320_at      1.000

In [16]:
# correlation heatmap

spearman_corr_matrix = eda.correlations(slice, type="spearman", printout="heatmap")

#### Boxplot examples

In [17]:

eda.box_plot(train_df, features=list(df.columns[9:]), stratify_var="Dukes Stage", group_var="Gender", title="Gene Expression of: ", xtitle="Gene", ytitle="Gene Expression Value", widget_description="Select: ", stratify=True, group=True)

In [18]:
# experimental.box_plot_v2(train_df, features=list(df.columns[9:]), categorical=df_cat)

In [19]:
# eda.box_plot(train_df, features=list(df.columns[9:]), stratify_var="", group_var="Gender", title="Gene Expression of: ", xtitle="Gene", ytitle="Gene Expression Value", widget_description="Select: ", stratify=False, group=True)

In [20]:
# eda.box_plot(train_df, features=list(df.columns[9:]), stratify_var="Dukes Stage", group_var="", title="Gene Expression of: ", xtitle="Dukes Stage", ytitle="Gene Expression Value", widget_description="Select: ", stratify=True, group=False)

In [21]:
# eda.box_plot(train_df, features=list(df.columns[9:]), stratify_var="Dukes Stage", group_var="Gender", title="Gene Expression of: ", xtitle="Dukes Stage", ytitle="Gene Expression Value", widget_description="Select: ", stratify=True, group=True)

In [22]:
# eda.box_plot(train_df, features=list(df.columns[9:]), stratify_var="Location", group_var="Gender", title="Gene Expression of: ", xtitle="Location", ytitle="Gene Expression Value", widget_description="Select: ", stratify=True, group=True)

In [23]:
# data sample for examples

gene_list = list(df.columns[9:])
gene_sample_list = gene_list[0:10]

In [24]:
eda.box_subplots(train_df, features=gene_sample_list, stratify_var="Location", columns=5, width=250, height=250, stratify=True)

#### Histogram examples

In [25]:
eda.hist_plot(train_df, features=list(df.columns[9:]), group_var="", title="Gene Expression Histogram of: ", xtitle="Gene Expression Value", ytitle="Count", widget_description="Select: ", group=False)

In [26]:
# eda.hist_plot(train_df, features=list(df.columns[9:]), group_var="Gender", title="Gene Expression Histogram of: ", xtitle="Gene Expression Value", ytitle="Count", widget_description="Select: ", group=True)

In [27]:
# eda.hist_plot(train_df, features=list(df.columns[9:]), group_var="Dukes Stage", title="Gene Expression Histogram of: ", xtitle="Gene Expression Value", ytitle="Count", widget_description="Select: ", group=True)

In [28]:
# eda.hist_plot(train_df, features=list(df.columns[9:]), group_var="Location", title="Gene Expression Histogram of: ", xtitle="Gene Expression Value", ytitle="Count", widget_description="Select: ", group=True)

In [29]:
# data sample for examples

gene_list = list(df.columns[9:])
gene_sample = train_df[gene_list].iloc[:,0:10]

In [30]:
eda.hist_subplots(gene_sample, columns=5, width=250, height=250)

#### Distribution plot examples

In [31]:
# data sample for examples

gene_list = list(df.columns[9:])
gene_sample = train_df[gene_list].iloc[:,0:10]

In [32]:
eda.dist_plot(gene_sample, title="Gene Expression Distribution Plot:")

In [33]:
eda.dist_subplots(gene_sample, columns=5, width=250, height=250)

#### Dimensionality Reduction

In [34]:
eda.pca_variance_plot(train_df, identifier=df_id, categorical=df_cat, continuous=df_cont, target="Dukes Stage")

In [35]:
train_df_encoded_2pca, train_df_2pca, test_df_encoded_2pca, test_df_2pca = eda.dimensionality_reduction(train_df, test_df, identifier=df_id, categorical=df_cat, continuous=df_cont, target="Dukes Stage", method="pca", plot_type="2d", components=2)

In [36]:
train_df_encoded_3pca, train_df_3pca, test_df_encoded_3pca, test_df_3pca = eda.dimensionality_reduction(train_df, test_df, identifier=df_id, categorical=df_cat, continuous=df_cont, target="Dukes Stage", method="pca", plot_type="3d", components=3)

In [37]:
# train_df_encoded_mds, train_df_mds, test_df_encoded_mds, test_df_mds = eda.dimensionality_reduction(train_df, test_df, identifier=df_id, categorical=df_cat, continuous=df_cont, target="Dukes Stage", method="mds", plot_type="multi", components=3)

In [38]:
# train_df_encoded_tsne, train_df_tsne, test_df_encoded_tsne, test_df_tsne = eda.dimensionality_reduction(train_df, test_df, identifier=df_id, categorical=df_cat, continuous=df_cont, target="Dukes Stage", method="tsne", plot_type="3d", components=3, perplexity=30)

In [39]:
# train_df_encoded_umap, train_df_umap, test_df_encoded_umap, test_df_umap = eda.dimensionality_reduction(train_df, test_df, identifier=df_id, categorical=df_cat, continuous=df_cont, target="Dukes Stage", method="umap", plot_type="3d", components=3, neighbors=100, min_distance=0.1, metric="mahalanobis")

#### Clustering

In [40]:
eda.kmeans_inertia_plot(train_df_2pca, identifier=df_id, target="Dukes Stage")

In [41]:
cluster_df = eda.clustering(df=train_df, input_df=train_df_2pca, identifier=df_id, target="Dukes Stage", method="kmeans", plot_type="2d", marker_size_ref="DFS (in months)", clusters=4, initializations=100, random_state=0)

In [42]:
cluster_df = eda.clustering(df=train_df, input_df=train_df_3pca, identifier=df_id, target="Dukes Stage", method="kmeans", plot_type="3d", marker_size_ref="DFS (in months)", clusters=4, initializations=100, random_state=0)

In [44]:
stage_names = ['A', 'B', 'C', 'D']
stage_data = {stage: df[df["Dukes Stage"]==stage] for stage in stage_names}

In [45]:
stage_data["A"]

ID_REF  Age (in years) Dukes Stage  Gender Location  DFS (in months)  \
0   GSM877126            62.0           A    Male     Left            108.0   
5   GSM877131            61.0           A    Male    Right             65.0   
12  GSM877138            47.0           A    Male    Right             81.0   
16  GSM877142            70.0           A    Male    Right            103.0   
17  GSM877143            67.0           A    Male    Right              4.0   
26  GSM877152            64.0           A  Female   Rectum             41.0   
30  GSM877156            69.0           A  Female   Rectum             39.0   
31  GSM877157            65.0           A    Male     Left             49.0   
36  GSM877162            61.0           A    Male    Right             46.0   
41  GSM877167            76.0           A    Male   Rectum             45.0   
45  GSM877171            73.0           A    Male    Right             24.0   
46  GSM877173            71.0           A    Male    Right             37.0   
51  GSM877178            59.0           A  Female     Left             22.0   
60  GSM877187            71.0           A    Male   Rectum             58.0   
61  GSM877188            57.0           A    Male   Rectum             68.0   

    DFS event  Adj_Radio  Adj_Chem    117_at  1007_s_at   1053_at    121_at  \
0         0.0        1.0       0.0  6.029834   9.468893  7.187090  6.807582   
5         0.0        1.0       1.0  6.863884   9.671754  7.040535  7.504727   
12        0.0        0.0       1.0  7.006106  10.033355  8.553709  7.730508   
16        1.0        0.0       1.0  6.004252   7.754544  6.795014  7.014675   
17        0.0        1.0       0.0  6.468004  10.214872  7.450276  7.205786   
26        1.0        0.0       0.0  7.480104  10.714543  7.301466  7.589869   
30        1.0        0.0       0.0  5.695817   9.841810  7.495638  7.017373   
31        1.0        0.0       1.0  5.350096  10.845055  7.256634  7.275098   
36        0.0        1.0       1.0  7.473647   9.655227  7.432907  7.036744   
41        0.0        1.0       0.0  5.142558  10.110382  7.522913  6.935763   
45        1.0        0.0       1.0  4.472217  10.610713  6.754314  7.512881   
46        1.0        0.0       0.0  5.618307  10.401409  6.968878  6.896913   
51        1.0        0.0       1.0  4.540863  10.003211  7.347620  7.744415   
60        1.0        1.0       0.0  5.702601  10.309094  7.476872  7.349701   
61        1.0        0.0       0.0  4.500368  10.996956  7.453162  8.031972   

    1255_g_at   1294_at   1316_at   1320_at  1405_i_at   1431_at   1438_at  \
0    3.084591  7.397013  6.525426  3.848253   7.572331  3.748200  6.957488   
5    2.772535  7.396619  6.466418  3.858941   8.292895  3.502790  6.700965   
12   2.953688  7.183682  6.294097  3.985674   9.058086  3.308840  7.604331   
16   3.242701  7.833150  5.453137  3.913796  10.774562  3.419892  5.053987   
17   2.969755  7.172667  6.345145  3.720011   8.988367  3.476634  6.992055   
26   3.072179  7.280062  5.391815  3.923898   8.060242  3.399339  8.501807   
30   2.822985  7.116496  6.220243  3.844773   7.196441  3.315586  6.368562   
31   2.745669  7.312673  5.940896  3.765223   6.279107  3.635534  6.758675   
36   3.022327  8.279301  5.344902  4.308143  10.057173  4.080034  7.666576   
41   3.377150  7.412063  5.804308  3.791204   7.795642  3.567524  8.827209   
45   3.010147  7.829368  6.216812  4.049242   7.263656  3.409415  8.631392   
46   2.885946  7.777051  6.428761  3.675192   8.638077  3.414836  7.709867   
51   3.049480  7.733358  5.614619  4.190360   9.033464  3.417822  6.481211   
60   2.858642  6.878941  6.137371  3.863878   8.280592  3.222998  7.979070   
61   2.787537  7.744197  5.793139  3.628732   6.951345  3.243738  7.859645   

     1487_at  1494_f_at  1552256_a_at  1552257_a_at  1552258_at  1552261_at  \
0   8.057704   4.311960      7.246198      8.998012    3.912720    4.206709   
5   7.608852   4.465112      7.804710      8.477863    4.044964    3.6

In [48]:
import plotly.graph_objects as go

help(go.Marker)

Help on class Marker in module plotly.graph_objs._deprecations:

class Marker(builtins.dict)
 |  Marker(*args, **kwargs)
 |  
 |      plotly.graph_objs.Marker is deprecated.
 |  Please replace it with one of the following more specific types
 |    - plotly.graph_objs.scatter.Marker
 |    - plotly.graph_objs.histogram.selected.Marker
 |    - etc.
 |  
 |  Method resolution order:
 |      Marker
 |      builtins.dict
 |      builtins.object
 |  
 |  Methods defined here:
 |  
 |  __init__(self, *args, **kwargs)
 |              plotly.graph_objs.Marker is deprecated.
 |      Please replace it with one of the following more specific types
 |        - plotly.graph_objs.scatter.Marker
 |        - plotly.graph_objs.histogram.selected.Marker
 |        - etc.
 |  
 |  ----------------------------------------------------------------------
 |  Data descriptors defined here:
 |  
 |  __dict__
 |      dictionary for instance variables (if defined)
 |  
 |  __weakref__
 |      list of weak reference

#### Experimental code

In [47]:
# histogram

# gene_list = list(df.columns[9:])
# gene_slice = gene_list[0:10]
# feature_list = []
# for feature in gene_list:
#     feature_list.append((feature, feature))

# import plotly.express as px
# import ipywidgets as widgets

# def fig_creator(selection):
#     fig = px.histogram(train_df, x=selection, color="Dukes Stage", facet_col="Dukes Stage")
#     fig.show()

# widgets.interact(fig_creator, selection=widgets.Dropdown(options=feature_list, description='Select:'));
